# Creation of the Calcium clusters


As an alternative for a calcium cut-off value a second way to devide the two calcium categories was proposed. This method is more context based and partly corrects for parity, farm and day of the calcium measurement. A linear mixed effect model was used combined with k-means clustering. As it is easier to program this in R the dataset was converted to R. 

In [ ]:
#Convert pyspark to R
pivotJoined_dataset.createOrReplaceTempView("R_scaled")

In [ ]:
#create dataframe
%r
require(SparkR)
Data_set_r <- sql("select * from R_scaled")
Data_set_r <- as.data.frame(Data_set_r)
head(Data_set_r)

In [ ]:
%r
#lineair mixed effect model, built in order to compensate for dependencies in the data > farm, parity, day of sampling 
install.packages("lme4")
install.packages("ggplot2")
library(ggplot2)
library(lme4)
library(dplyr)
AnalysisDataCluster <- Data_set_r %>% 
dplyr::select(
    CalciumValue,
    CalciumDaysInMilk,
    Parity,
    AnimalEartag,
    HerdIdentifier)

#define model
ClusterLMER<-lme4::lmer(
                  CalciumValue ~ CalciumDaysInMilk * Parity +  (1| HerdIdentifier), 
                  data = AnalysisDataCluster,
                  REML = FALSE
                  )

#predict calcium
AnalysisDataCluster$PredictCalcium <- predict(ClusterLMER, newdata = AnalysisDataCluster)
AnalysisDataCluster$CalciumResidual <- residuals(ClusterLMER)
#k-means clustering
AnalysisDataCluster$CalciumCluster <- as.factor(kmeans(AnalysisDataCluster[,c("CalciumValue","CalciumResidual")],centers=2)$cluster)
#plot calcium vs residuals with clustering 
ggplot(AnalysisDataCluster,
aes(x=CalciumValue, y=CalciumResidual, colour = CalciumCluster))  +
geom_point() +
scale_color_manual(breaks = c('1','2'),
                   values=c("gray20", "gray89")) +
theme_classic()

In [ ]:
%r
#when numbers of observations are limited, a binary variable is easier to predict. Therefore the clustering is used as a binary variable
Calciumcluster <- AnalysisDataCluster$CalciumCluster 
#add clusters to dataframe
data_set_r2 <- cbind(Data_set_r, Calciumcluster)
#change name of cluster 2 to 0 = not at risk and 1 stays 1  = at risk of hypocalceamia
levels(data_set_r2$Calciumcluster) <- c(1,0)
summary(data_set_r2$Calciumcluster)

In [ ]:
%r
#convert dataframe from r back to python 
data_set_levels <- as.DataFrame(data_set_r2)

createOrReplaceTempView(data_set_levels,"r_back_to_py")

In [ ]:
Data_set_from_r = sql("SELECT * FROM r_back_to_py") 

#Add missing rows, missing values result in missing rows which need to be imputed. 

In [ ]:
Data_set_from_r = Data_set_from_r.toPandas()
#convert pyspark dataframe to panda dataframe

In [ ]:
#Only keep scores for the end of dry period, because scores from different time points are incomparable 
panda_data_set['FirstLocomotionScore'].mask(panda_data_set['FirstLocomotionType'] != 'LocomotionScoreEndDryPeriod', 0, inplace=True)
panda_data_set['FirstBCSScore'].mask(panda_data_set['FirstBCSType'] != 'BCSEndDryPeriod', 0, inplace=True)

In [ ]:
import pandas as pd
#extract unique cows and the static features that belong to that cow and are never missing 
unique_calvings = panda_data_set[['AnimalEartag', 'PaperRecordedCalvingDate']].drop_duplicates() 
Cluster_lijst = []
CalciumValue_lijst = []
season_lijst = []
calindays_lijst = []
parity_lijst = []
HerdIdentifier_lijst = []

#filter through dataset 
for index, (AnimalEartag, PaperRecordedCalvingDate) in unique_calvings.iterrows():
    filter1 = panda_data_set['AnimalEartag'] == AnimalEartag
    filter2 = PaperRecordedCalvingDate == panda_data_set['PaperRecordedCalvingDate']
    gefilterde_set = panda_data_set[filter1 & filter2]
    Parity = gefilterde_set['Parity'].iloc[-1]
    HerdIdentfier = gefilterde_set['HerdIdentifier'].iloc[-1]
    Calindays = gefilterde_set['CalciumDaysInMilk'].iloc[-1]
    season = gefilterde_set['CalvingSeason'].iloc[-1] 
    Calcium_cluster = gefilterde_set['Calciumcluster'].iloc[-1]
    Calcium_Value = gefilterde_set['CalciumValue'].iloc[-1]
    Cluster_lijst.append((Calcium_cluster)) 
    CalciumValue_lijst.append((Calcium_Value))
    season_lijst.append((season))
    calindays_lijst.append(Calindays)
    parity_lijst.append(Parity)
    HerdIdentifier_lijst.append(HerdIdentfier)
#add to list and dataframe    
Calcium_df = pd.DataFrame (Cluster_lijst, columns = ['Calciumcluster'])  
Calcium_df['CalciumValue'] = CalciumValue_lijst
Calcium_df['CalvingSeason'] = season_lijst
Calcium_df['Parity'] = parity_lijst
Calcium_df['CalciumDaysInMilk'] = calindays_lijst
Calcium_df['HerdIdentifier'] = HerdIdentifier_lijst


In [ ]:
#Some cows had two rows for the same day, solved by group-by
data_set_bijna_compleet = panda_data_set.groupby(['AnimalEartag','PaperRecordedCalvingDate','TransitionDaysInMilk'], as_index = False) \
.sum(["WalkingTimeMinutesPerDay", "EatingBoutLengthMinutesPerBout", "EatingInterBoutLengthMinutes", "EatingNumberOfBoutsPerDay", "EatingTimeMinutesPerDay", "InactiveBoutLengthMinutesPerDay", "InactiveBoutsPerDay", "InactiveInterboutLengthMinutesPerDay", "InactiveTimeMinutesPerDay", "LegActivityStepsPerDay", "LyingBoutLengthMinutesPerDay","LyingBoutsPerDay", "LyingTimeMinutesPerDay", "RuminationBoutLengthMinutesPerBout", "RuminationInterBoutLengthMinutes", "RuminationNumberOfBoutsPerDay","RuminationTimeMinutesPerDay", "StandingTimeMinutesPerDay", "StandupsPerDay"])
#groupby caused columns to go missing, re-added by a left merge with the old dataframe 
data_set_bijna_compleet = pd.merge(data_set_bijna_compleet, panda_data_set, on = ['AnimalEartag', 'PaperRecordedCalvingDate', 'TransitionDaysInMilk', "WalkingTimeMinutesPerDay", "EatingBoutLengthMinutesPerBout", "EatingInterBoutLengthMinutes", "EatingNumberOfBoutsPerDay", "EatingTimeMinutesPerDay", "InactiveBoutLengthMinutesPerDay", "InactiveBoutsPerDay", "InactiveInterboutLengthMinutesPerDay", "InactiveTimeMinutesPerDay", "LegActivityStepsPerDay", "LyingBoutLengthMinutesPerDay","LyingBoutsPerDay", "LyingTimeMinutesPerDay", "RuminationBoutLengthMinutesPerBout", "RuminationInterBoutLengthMinutes", "RuminationNumberOfBoutsPerDay","RuminationTimeMinutesPerDay", "StandingTimeMinutesPerDay", "StandupsPerDay", "HerdIdentifier", "LactationNumber", "FirstLocomotionScore", 'FirstBCSScore', 'DryOffBCS', 'CalciumValue', 'KetosisValueOne', 'KetosisValueTwo', 'BCSEndDryMinusDryOff', 'DryPeriodLength', 'LocomotionDaysInMilk', 'BCSDaysInMilk', 'CalciumDaysInMilk', 'KetosisOneDaysInMilk', 'KetosisTwoDaysInMilk', "Year", "AnimalIdentifier"], how = 'left')

In [ ]:
#extract BCS and Loco scores
grouped_set = panda_data_set.groupby(['AnimalEartag', 'PaperRecordedCalvingDate']).max(['FirstBCSScore', 'FirstLocomotionScore'])
BCSandLoco = grouped_set[['FirstBCSScore', 'FirstLocomotionScore']]

In [ ]:
#insert rows, every cow must have 21 rows and 19 features 
import pandas as pd
import numpy as np
unique_calvings = data_set_bijna_compleet[['AnimalEartag', 'PaperRecordedCalvingDate']].drop_duplicates() #609 unique cows
unique_calvings.reset_index(drop=True, inplace=True)
Calcium_df.reset_index(drop=True, inplace=True)
BCSandLoco.reset_index(drop = True, inplace = True)

columns_to_transform = ["WalkingTimeMinutesPerDay", "EatingBoutLengthMinutesPerBout", "EatingInterBoutLengthMinutes", "EatingNumberOfBoutsPerDay", "EatingTimeMinutesPerDay", "InactiveBoutLengthMinutesPerDay", "InactiveBoutsPerDay", "InactiveInterboutLengthMinutesPerDay", "InactiveTimeMinutesPerDay", "LegActivityStepsPerDay", "LyingBoutLengthMinutesPerDay","LyingBoutsPerDay", "LyingTimeMinutesPerDay", "RuminationBoutLengthMinutesPerBout", "RuminationInterBoutLengthMinutes", "RuminationNumberOfBoutsPerDay","RuminationTimeMinutesPerDay", "StandingTimeMinutesPerDay", "StandupsPerDay"]

new_column = [*range(-20,1)]

unique_calvings['TransitionDaysInMilk'] = pd.Series([new_column for x in range(len(unique_calvings.index))]).values
unique_calvings = unique_calvings.join(Calcium_df, how = 'left')
unique_calvings_clus = unique_calvings.join(BCSandLoco, how = 'left')
right_df = unique_calvings_clus.groupby(['AnimalEartag', 'PaperRecordedCalvingDate','Calciumcluster', 'CalciumValue', 'CalvingSeason', 'CalciumDaysInMilk', 'Parity', 'FirstBCSScore', 'FirstLocomotionScore', 'HerdIdentifier']).TransitionDaysInMilk.apply(lambda x: pd.DataFrame(x.values[0])).reset_index()
right_df = right_df.drop('level_10', axis=1)
right_df.columns = ['AnimalEartag', 'PaperRecordedCalvingDate', 'Calciumcluster', 'CalciumValue', 'CalvingSeason', 'CalciumDaysInMilk', 'Parity', 'FirstBCSScore', 'FirstLocomotionScore', 'HerdIdentifier', 'TransitionDaysInMilk']
panda_set_compleet = pd.merge(right_df, data_set_bijna_compleet, on = ['AnimalEartag', 'PaperRecordedCalvingDate',  'TransitionDaysInMilk'], how = 'left')
panda_set_compleet['Calciumcluster'] = right_df['Calciumcluster']
panda_set_compleet['CalciumValue'] = right_df['CalciumValue']
panda_set_compleet['CalvingSeason'] = right_df['CalvingSeason']
panda_set_compleet['Parity'] = right_df['Parity']
panda_set_compleet['CalciumDaysInMilk'] = right_df['CalciumDaysInMilk']
panda_set_compleet['FirstLocomotionScore'] = right_df['FirstLocomotionScore']
panda_set_compleet['FirstBCSScore'] = right_df['FirstBCSScore']
panda_set_compleet['HerdIdentifier'] = right_df['HerdIdentifier']
panda_set_compleet = panda_set_compleet.drop(['Calciumcluster_y', 'Calciumcluster_x', 'CalciumValue_x', 'CalciumValue_y', 'CalvingSeason_x', 'CalvingSeason_y', 'CalciumDaysInMilk_x', 'CalciumDaysInMilk_y', 'Parity_x', 'Parity_y', 'FirstLocomotionScore_x', 'FirstLocomotionScore_y', 'FirstBCSScore_x', 'FirstBCSScore_y', 'HerdIdentifier_x', 'HerdIdentifier_y'], axis =1)
panda_set_compleet[columns_to_transform] = panda_set_compleet[columns_to_transform].replace(0, np.nan) #zodat 0 null wordt
display(panda_set_compleet)

AnimalEartag PaperRecordedCalvingDate Calciumcluster TransitionDaysInMilk LactationNumber DryOffBCS KetosisValueOne KetosisValueTwo BCSEndDryMinusDryOff DryPeriodLength LocomotionDaysInMilk BCSDaysInMilk KetosisOneDaysInMilk KetosisTwoDaysInMilk AnimalIdentifier Year WalkingTimeMinutesPerDay EatingBoutLengthMinutesPerBout EatingInterBoutLengthMinutes EatingNumberOfBoutsPerDay EatingTimeMinutesPerDay InactiveBoutLengthMinutesPerDay InactiveBoutsPerDay InactiveInterboutLengthMinutesPerDay InactiveTimeMinutesPerDay LegActivityStepsPerDay LyingBoutLengthMinutesPerDay LyingBoutsPerDay LyingTimeMinutesPerDay RuminationBoutLengthMinutesPerBout RuminationInterBoutLengthMinutes RuminationNumberOfBoutsPerDay RuminationTimeMinutesPerDay StandingTimeMinutesPerDay StandupsPerDay CalvingDate FirstLocomotionScoreDate FirstLocomotionType FirstBCSDate FirstBCSType DryOffDate CalciumDate KetosisDateOne KetosisDateTwo CalciumValue CalvingSeason Parity CalciumDaysInMilk FirstLocomotionScore FirstBCSScore HerdIdentifier NL340704985 2017-05-21T00:00:00.000+0000 0 -21 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 25.0 15.0 129.0 10.0 159.0 32.0 23.0 28.0 746.0 2852.0 120.0 6.0 736.0 31.0 58.0 16.0 535.0 679.0 9.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -20 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 27.0 17.0 123.0 11.0 190.0 40.0 19.0 33.0 778.0 2907.0 124.0 6.0 714.0 33.0 65.0 14.0 472.0 699.0 6.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -19 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 53.0 16.0 98.0 12.0 208.0 30.0 23.0 29.0 716.0 5076.0 105.0 5.0 566.0 28.0 55.0 18.0 499.0 821.0 8.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -18 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 30.0 19.0 147.0 8.0 158.0 37.0 22.0 28.0 821.0 3286.0 129.0 5.0 657.0 33.0 73.0 13.0 461.0 753.0 6.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -17 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 30.0 15.0 177.0 8.0 130.0 42.0 18.0 33.0 775.0 2878.0 82.0 10.0 741.0 39.0 67.0 14.0 535.0 669.0 10.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -16 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9.0 16.0 9.0 2017.0 27.0 17.0 170.0 8.0 149.0 37.0 20.0 36.0 744.0 2991.0 95.0 6.0 648.0 34.0 56.0 15.0 547.0 765.0 7.0 2017-05-21T00:00:00.000+0000 2017-05-16T00:00:00.000+0000 LocomotionScoreEndDryPeriod 2017-05-16T00:00:00.000+0000 BCSEndDryPeriod 2017-04-18T00:00:00.000+0000 2017-05-23T00:00:00.000+0000 2017-05-30T00:00:00.000+0000 2017-06-06T00:00:00.000+0000 2.23 Spring 3+ 2 4.0 2.25 2297 NL340704985 2017-05-21T00:00:00.000+0000 0 -15 13.0 2.0 2.0 4.2 0.25 33.0 -5.0 -5.0 9

In [ ]:
#add column with cut-off value #cut-off value based on: Prevalence of subclinical hypocalcemia in dairy herds by Reinhardt
panda_set_compleet['Cut_Off'] = np.where(panda_set_compleet['CalciumValue']<= 2.0, '1', '0')
